In [ ]:
import pandas as pd

In [ ]:
import numpy as np

In [ ]:
dataFile = pd.read_csv("/content/drive/MyDrive/IR Assignment 2 /ASSIGNMENT2_DATA.csv")

# Question 1

 Load the Necessary Libraries

In [ ]:
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.applications.resnet50 import preprocess_input
from tensorflow.keras.preprocessing.image import img_to_array
from tensorflow.keras.applications import ResNet50
from sklearn.feature_extraction.text import TfidfVectorizer
import requests
from PIL import Image, ImageEnhance
import io
import random
import pickle


load Images from the urls

In [ ]:
def load_image_from_url(image_url):
    try:
        response = requests.get(image_url)
        return Image.open(io.BytesIO(response.content))
    except Exception as e:
        print(f"Error loading image from URL: {image_url}")
        return None

Apply some random flips

In [ ]:
def apply_random_flips(image):
    if random.choice([True, False]):
        image = image.transpose(Image.FLIP_LEFT_RIGHT)
    if random.choice([True, False]):
        image = image.transpose(Image.FLIP_TOP_BOTTOM)
    return image

Adjust the Brightness

In [ ]:
def adjust_brightness(image):
    enhancer = ImageEnhance.Brightness(image)
    return enhancer.enhance(random.uniform(0.5, 1.5))


Resize the images

In [ ]:
def resize_image(image, target_size=(224, 224)):
    return image.resize(target_size)


Make the dimesions suitable for restNet

In [ ]:

def preprocess_image_for_resnet(image):
    image_array = img_to_array(image)
    preprocessed_image = preprocess_input(np.expand_dims(image_array, axis=0))
    return preprocessed_image

Extract Image Feature using the restnet

In [ ]:
def extract_image_features(image_url, model):
    try:
        image = load_image_from_url(image_url)
        if image is None:
            return None

        image = apply_random_flips(image)
        image = adjust_brightness(image)
        image = resize_image(image)
        preprocessed_image = preprocess_image_for_resnet(image)

        # Extract features using the provided ResNet model
        features = model.predict(preprocessed_image)
        features = features.flatten()

        return features
    except Exception as e:
        print(f"Error processing image at URL: {image_url}")
        return None

Normalize the Feature

In [ ]:


def normalize_features(features):
    return features / np.linalg.norm(features)


Save into the Pickle file

In [ ]:

def save_features_to_pickle(features, output_path):
    with open(output_path, 'wb') as f:
        pickle.dump(features, f)

In [ ]:
# Load pre-trained ResNet50 model
resnet_model = ResNet50(weights='imagenet', include_top=False)


94765736/94765736 [==============================] - 0s 0us/step


In [ ]:

# # Apply image feature extraction to each image in the dataset
# image_features = {}
# for index, row in dataFile.iterrows():
#     image_urls = eval(row['Image'])  # Convert string representation of list to list
#     features_list = []
#     for image_url in image_urls:
#         features = extract_image_features(image_url, resnet_model)
#         if features is not None:
#             image_features[image_url] = normalize_features(features)
#             features_list.append(features)
#     dataFile.at[index, 'Features'] = str(features_list)

# # Save the extracted features using pickle in the desired directory
# output_pickle_path = "/content/drive/MyDrive/IR Assignment 2/Images_Pickle"
# save_features_to_pickle(image_features, output_pickle_path)

# print("Image feature extraction completed and features saved.")



# Question 2
## Text Preprocessing and Save into the pickle file

In [ ]:
import pandas as pd
import numpy as np
import re
import nltk
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer
import math
import pickle

In [ ]:

# Download NLTK resources
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


True

### Text Preprocessing Functions


In [ ]:

def convert_to_lowercase(text):
    """Converts text to lowercase."""
    return text.lower()

In [ ]:

def tokenize_text(text):
    """Tokenizes text using NLTK."""
    return nltk.word_tokenize(text)


In [ ]:
def remove_punctuation(tokens):
    """Removes punctuation and non-alphanumeric characters from tokens."""
    return [re.sub(r'[^a-zA-Z0-9]', '', token) for token in tokens]

In [ ]:

def remove_stopwords(tokens):
    """Removes stopwords using NLTK."""
    stop_words = set(stopwords.words('english'))
    return [token for token in tokens if token not in stop_words]


In [ ]:


def apply_stemming(tokens):
    """Applies stemming using Porter Stemmer."""
    stemmer = PorterStemmer()
    return [stemmer.stem(token) for token in tokens]


In [ ]:
def apply_lemmatization(tokens):
    """Applies lemmatization using WordNet Lemmatizer."""
    lemmatizer = WordNetLemmatizer()
    return [lemmatizer.lemmatize(token) for token in tokens]


In [ ]:
def apply_beautiful_soup(html_text):
    """Applies BeautifulSoup to extract text from HTML."""
    if isinstance(html_text, str):
        soup = BeautifulSoup(html_text, 'html.parser')
        # Extract text from the HTML
        text = soup.get_text()
        # Remove extra whitespaces and newlines
        text = re.sub(r'\s+', ' ' , text).strip()
        return text
    else:
        return ""


In [ ]:
from bs4 import BeautifulSoup
import re

def preprocess_text(text):
    """Applies a series of text pre-processing steps."""
    if isinstance(text, str):
        text = apply_beautiful_soup(text)
        text = convert_to_lowercase(text)
        tokens = tokenize_text(text)
        tokens = remove_punctuation(tokens)
        tokens = remove_stopwords(tokens)
        tokens = apply_stemming(tokens)
        tokens = apply_lemmatization(tokens)
        return tokens
    else:
        return []


# # Define other preprocessing functions (convert_to_lowercase, tokenize_text, remove_punctuation, etc.)

# # Example usage:
# html_content = "<html><body><h1>Hello, World!</h1><p>This is a sample HTML content.</p></body></html>"
# preprocessed_tokens = preprocess_text(html_content)
# print(preprocessed_tokens)


In [ ]:

# Apply text pre-processing to each review in the dataset
corpus = dataFile['Review Text']


In [ ]:
print(type(corpus))

<class 'pandas.core.series.Series'>


In [ ]:
for review in corpus:
  print(f'{review}\n')

Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.

Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.

We use these for everything from our acoustic bass down to our ukuleles. I know there is a smaller model available for ukes, violins, etc.; we haven't yet ordered those, but these will work on smaller instruments if one doesn't extend the feet to their maximum width. They're gentle on the instruments, and the grippy material keeps them secure.

The greatest benefit has been when writing music at the computer and needing to set a guitar down to use the keyboard/mouse - just easier for me than a hanging stand.

We have several and gave one to a friend for Christmas as well. I've used

In [ ]:

# def tokenize_documents(corpus):
#     return [preprocess_text(doc) for doc in corpus]


In [ ]:
# def calculate_term_frequency(tokenized_docs):
#     tf_docs = []
#     for doc in tokenized_docs:
#         tf_doc = {}
#         word_count = len(doc)
#         word_freq = Counter(doc)
#         for word, freq in word_freq.items():
#             tf_doc[word] = freq / word_count
#         tf_docs.append(tf_doc)
#     return tf_docs


In [ ]:
# def calculate_inverse_document_frequency(term, allDocuments):
#     numDocumentsWithThisTerm = sum(1 for doc in allDocuments if term in doc)
#     if numDocumentsWithThisTerm > 0:
#         return 1.0 + math.log(len(allDocuments) / numDocumentsWithThisTerm)
#     else:
#         return 1.0

In [ ]:
# 'def calculate_idf(tokenized_docs):
#     idf_dict = {}
#     for doc in tokenized_docs:
#         for word in set(doc):
#             idf_dict[word] = calculate_inverse_document_frequency(word, tokenized_docs)
#     return idf_dict
# '

In [ ]:

# def calculate_tfidf(tokenized_docs, tf_docs, idf_dict):
#     tfidf_docs = []
#     for doc, tf_doc in zip(tokenized_docs, tf_docs):
#         tfidf_doc = {}
#         for word, tf in tf_doc.items():
#             tfidf_doc[word] = tf * idf_dict[word]
#         tfidf_docs.append(tfidf_doc)
#     return tfidf_docs


In [ ]:
# def print_tfidf(tfidf_docs):
#     for i, tfidf_doc in enumerate(tfidf_docs):
#         print(f"Document {i+1}: {tfidf_doc}\n")


In [ ]:


# # Main function
# def main(corpus):
#     tokenized_docs = tokenize_documents(corpus)
#     tf_docs = calculate_term_frequency(tokenized_docs)
#     idf_dict = calculate_idf(tokenized_docs)
#     print(f'This is idf Dictionary{idf_dict}\n')
#     tfidf_docs = calculate_tfidf(tokenized_docs, tf_docs, idf_dict)
#     print(f'This is tdfidf Dictionary{tfidf_docs}\n')
#     print_tfidf(tfidf_docs)




In [ ]:
print(corpus)

0      Loving these vintage springs on my vintage str...
1      Works great as a guitar bench mat. Not rugged ...
2      We use these for everything from our acoustic ...
3      Great price and good quality.  It didn't quite...
4      I bought this bass to split time as my primary...
                             ...                        
995                   Extremely impressed with this kit.
996    This is a great stereo reverb with plenty of c...
997    I really like the simplicity of this bridge. I...
998    Great Product, but there is no warranty in the...
999    This product is good and is used in profession...
Name: Review Text, Length: 1000, dtype: object


In [ ]:
def find_similar_sentences(new_sentence, corpus, top_n=3):
    preprocessed_new_sentence = preprocess_text(new_sentence)
    corpus1.append(preprocessed_new_sentence)

    # Calculate TF-IDF vectors
    tfidf_vectorizer = TfidfVectorizer()
    tfidf_matrix = tfidf_vectorizer.fit_transform(corpus)

    # Calculate cosine similarity between new sentence and corpus
    similarity_scores = cosine_similarity(tfidf_matrix[-1], tfidf_matrix[:-1])[0]

    # Get indices of top similar sentences
    top_indices = similarity_scores.argsort()[-top_n:][::-1]

    # Return top similar sentences and their similarity scores
    similar_sentences = [(corpus[idx], similarity_scores[idx]) for idx in top_indices]

    return similar_sentences

In [ ]:
corpus

0      Loving these vintage springs on my vintage str...
1      Works great as a guitar bench mat. Not rugged ...
2      We use these for everything from our acoustic ...
3      Great price and good quality.  It didn't quite...
4      I bought this bass to split time as my primary...
                             ...                        
995                   Extremely impressed with this kit.
996    This is a great stereo reverb with plenty of c...
997    I really like the simplicity of this bridge. I...
998    Great Product, but there is no warranty in the...
999    This product is good and is used in profession...
Name: Review Text, Length: 1000, dtype: object

In [ ]:
# main()

In [ ]:
# import math
# from collections import Counter



# tokenized_docs = [preprocess_text(doc) for doc in corpus]

# # Calculate Term Frequency (TF) for each token in each document
# tf_docs = []
# for doc in tokenized_docs:
#     tf_doc = {}
#     word_count = len(doc)
#     word_freq = Counter(doc)
#     for word, freq in word_freq.items():
#         tf_doc[word] = freq / word_count
#     tf_docs.append(tf_doc)

# # Calculate Inverse Document Frequency (IDF) for each token
# def inverseDocumentFrequency(term, allDocuments):
#     numDocumentsWithThisTerm = sum(1 for doc in allDocuments if term in doc)
#     if numDocumentsWithThisTerm > 0:
#         return 1.0 + math.log(len(allDocuments) / numDocumentsWithThisTerm)
#     else:
#         return 1.0

# idf_dict = {}
# for doc in tokenized_docs:
#     for word in set(doc):
#         idf_dict[word] = inverseDocumentFrequency(word, tokenized_docs)

# # Calculate TF*IDF for each token in each document
# tfidf_docs = []
# for doc, tf_doc in zip(tokenized_docs, tf_docs):
#     tfidf_doc = {}
#     for word, tf in tf_doc.items():
#         tfidf_doc[word] = tf * idf_dict[word]
#     tfidf_docs.append(tfidf_doc)

# # Print TF*IDF for each document
# for i, tfidf_doc in enumerate(tfidf_docs):
#     print(f"Document {i+1}: {tfidf_doc}\n")
import math
from collections import Counter

# # Dummy function for text preprocessing (replace with your actual preprocessing function)
# def preprocess_text(doc):
#     return doc.lower().split()  # Dummy tokenization (splitting by whitespace and lowercasing)

# Dummy corpus (replace with your actual corpus)

# Tokenize the documents in the corpus
tokenized_docs = [preprocess_text(doc) for doc in corpus]

# Calculate Term Frequency (TF) for each token in each document
tf_docs = []
for doc in tokenized_docs:
    tf_doc = {}
    word_count = len(doc)
    word_freq = Counter(doc)
    for word, freq in word_freq.items():
        tf_doc[word] = freq / word_count
    tf_docs.append(tf_doc)

# Calculate Inverse Document Frequency (IDF) for each token
def inverseDocumentFrequency(term, allDocuments):
    numDocumentsWithThisTerm = sum(1 for doc in allDocuments if term in doc)
    if numDocumentsWithThisTerm > 0:
        return 1.0 + math.log(len(allDocuments) / numDocumentsWithThisTerm)
    else:
        return 1.0

idf_dict = {}
for doc in tokenized_docs:
    for word in set(doc):
        idf_dict[word] = inverseDocumentFrequency(word, tokenized_docs)

# Calculate TF*IDF for each token in each document
tfidf_docs = []
for doc, tf_doc in zip(tokenized_docs, tf_docs):
    tfidf_doc = {}
    for word, tf in tf_doc.items():
        tfidf_doc[word] = tf * idf_dict[word]
    tfidf_docs.append(tfidf_doc)

# Print TF*IDF numerical values for each document
for i, tfidf_doc in enumerate(tfidf_docs):
    tfidf_values = list(tfidf_doc.values())
    print(f"Document {i+1}: {tfidf_values}\n")


<ipython-input-22-361e47dfb45c>:4: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_text, 'html.parser')


Document 1: [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622]

Document 2: [0.08501164029173598, 0.07377359597201258, 0.07801063383927238, 0.2487795896007652, 0.2487795896007652, 0.17731025422787897, 0.1969148517808937, 0.12201060091431433, 0.23479803414875958, 0.2596290036269382, 0.3085357292756546, 0.1048352009836743, 0.21718335746717365, 0.2726812165166254, 0.10906286726272024, 0.16938010363545333, 0.1261813805838889, 0.1510825777367578, 0.0719887016768888, 0.2009763357690449, 0.1303662377219671, 0.1344973135775747, 0.08896134862732952]

Document 3: [0.08690719194238329, 0.057124461105462584, 0.056487200617313355, 0.050523939367205895, 0.06369395535562541, 0.1972272964836133, 0.054198788498639856, 0.13074687843980787, 0.06317696456133982, 0.07318912

In [ ]:
# Create the final dictionary
# final_dict = {}

# # Iterate over preprocessed text and TF-IDF scores
# for text, tfidf_doc in zip(corpus, tfidf_docs):
#     # Join the preprocessed text tokens back into a string
#     preprocessed_text = ' '.join(preprocess_text(text))
#     # Add the preprocessed text and its corresponding TF-IDF scores to the final dictionary
#     final_dict[preprocessed_text] = tfidf_doc

# # Print the final dictionary
# for text, tfidf_scores in final_dict.items():
#     print(f"Text: {text}\nTF-IDF Scores: {tfidf_scores}\n")
# Create the final dictionary
final_dict = {}

# Iterate over preprocessed text and TF-IDF scores
for text, tfidf_doc in zip(corpus, tfidf_docs):
    # Join the preprocessed text tokens back into a string
    preprocessed_text = ' '.join(preprocess_text(text))
    # Get only the numerical TF-IDF scores
    numerical_tfidf = {word: score for word, score in tfidf_doc.items() if isinstance(score, (int, float))}
    # Add the preprocessed text and its corresponding numerical TF-IDF scores to the final dictionary
    final_dict[text] = numerical_tfidf

# Print the final dictionary
for text, tfidf_scores in final_dict.items():
    print(f"Text: {text}\nNumerical TF-IDF Scores: {tfidf_scores}\n")


<ipython-input-22-361e47dfb45c>:4: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(html_text, 'html.parser')


Text: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
Numerical TF-IDF Scores: {'love': 0.17063740955725884, 'vintag': 0.5574870578984413, 'spring': 0.6624272366585359, 'strat': 0.2290869802813264, '': 0.171399912420283, 'good': 0.14332661723291976, 'tension': 0.32379520762790565, 'great': 0.11885746017713138, 'stabil': 0.32379520762790565, 'float': 0.3782857216841126, 'bridg': 0.24341081968699865, 'want': 0.17523139377087624, 'way': 0.20096087987965253, 'go': 0.1719761624227622}

Text: Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.
Numerical TF-IDF Scores: {'work': 0.08501164029173598, 'great': 0.07377359597201258, 'guitar': 0.07801063383927238, 'bench': 0.2487795896007652, '

In [ ]:
print(final_dict)

{'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.': {'love': 0.17063740955725884, 'vintag': 0.5574870578984413, 'spring': 0.6624272366585359, 'strat': 0.2290869802813264, '': 0.171399912420283, 'good': 0.14332661723291976, 'tension': 0.32379520762790565, 'great': 0.11885746017713138, 'stabil': 0.32379520762790565, 'float': 0.3782857216841126, 'bridg': 0.24341081968699865, 'want': 0.17523139377087624, 'way': 0.20096087987965253, 'go': 0.1719761624227622}, "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.": {'work': 0.08501164029173598, 'great': 0.07377359597201258, 'guitar': 0.07801063383927238, 'bench': 0.2487795896007652, 'mat': 0.2487795896007652, '': 0.17731025422787897, 'rug

In [ ]:

result_dict = {}

for key, text_data in final_dict.items():
    numerical_values = list(text_data.values())
    result_dict[key] = numerical_values

print(result_dict)


{'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.': [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622], "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.": [0.08501164029173598, 0.07377359597201258, 0.07801063383927238, 0.2487795896007652, 0.2487795896007652, 0.17731025422787897, 0.1969148517808937, 0.12201060091431433, 0.23479803414875958, 0.2596290036269382, 0.3085357292756546, 0.1048352009836743, 0.21718335746717365, 0.2726812165166254, 0.1090

In [ ]:
import os
import pickle

# Define the directory path
directory_path = "/content/drive/MyDrive/IR Assignment 2 "

# Ensure that the directory exists, if not create it
if not os.path.exists(directory_path):
    os.makedirs(directory_path)

# Define the output pickle file path
output_pickle_path = os.path.join(directory_path, "finalDictUpdated_Pickle.pkl")

# Function to save dictionary to pickle file
def save_to_pickle(data, file_path):
    with open(file_path, 'wb') as file:
        pickle.dump(data, file)

# Save the final_dict dictionary in a pickle file
save_to_pickle(result_dict, output_pickle_path)

print(f"Final dictionary saved to {output_pickle_path}")


Final dictionary saved to /content/drive/MyDrive/IR Assignment 2 /finalDictUpdated_Pickle.pkl


In [ ]:
import os

# Get the size of the pickle file in bytes
pickle_file_size_bytes = os.path.getsize('/content/drive/MyDrive/IR Assignment 2 /finalDictUpdated_Pickle.pkl')

# Convert bytes to megabytes
pickle_file_size_mb = pickle_file_size_bytes / (1024 * 1024)  # 1 MB = 1024 * 1024 bytes

# Print the size of the pickle file
print(f"Size of the pickle file: {pickle_file_size_mb:.2f} MB")


Size of the pickle file: 0.69 MB


In [ ]:
# imageFeature = /content/drive/MyDrive/IR Assignment 2 /Images_Pickle
# tfidfScore = /content/drive/MyDrive/IR Assignment 2 /final_dict.pkl


In [ ]:
import pickle

# Define the file paths
image_feature_path = "/content/drive/MyDrive/IR Assignment 2 /Images_Pickle"
tfidf_score_path = "/content/drive/MyDrive/IR Assignment 2 /finalDictUpdated_Pickle.pkl"

# Load the pickle files
with open(image_feature_path, 'rb') as file:
    image_features = pickle.load(file)

with open(tfidf_score_path, 'rb') as file:
    tfidf_scores = pickle.load(file)

# # Print the structure of the head of the loaded data
# print("Structure of Image Features:")
# print(image_features[:5])

# print("\nStructure of TF-IDF Scores:")
# print(list(tfidf_scores.items())[:5])


In [ ]:
print(f'Images Feature Pickle File Format {type(image_features)}')

Images Feature Pickle File Format <class 'dict'>


# Format of My Image Pickle

In [ ]:
# Print the first 5 key-value pairs of the image_features dictionary
for key, value in list(image_features.items())[:5]:
    print(f"Key: {key}\nValue: {value}\n")


Key: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
Value: [0.         0.01246884 0.         ... 0.         0.         0.        ]

Key: https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg
Value: [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 8.240409e-05
 0.000000e+00]

Key: https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg
Value: [0. 0. 0. ... 0. 0. 0.]

Key: https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg
Value: [0.         0.         0.         ... 0.         0.00507829 0.        ]

Key: https://images-na.ssl-images-amazon.com/images/I/71Md5ihUFLL._SY88.jpg
Value: [0. 0. 0. ... 0. 0. 0.]



# Format of my Text Pickle

In [ ]:
print(len(tfidf_scores))

997


In [ ]:
# print(type(tfidf_scores))
for key, value in list(tfidf_scores.items())[:5]:
    print(f"Key: {key}\nValue: {value}\n")

Key: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
Value: [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622]

Key: Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too.
Value: [0.08501164029173598, 0.07377359597201258, 0.07801063383927238, 0.2487795896007652, 0.2487795896007652, 0.17731025422787897, 0.1969148517808937, 0.12201060091431433, 0.23479803414875958, 0.2596290036269382, 0.3085357292756546, 0.1048352009836743, 0.21718335746717365, 0.2726812

## Testing for Question 3

In [ ]:

# File paths
dataset_path = "/content/drive/MyDrive/IR Assignment 2 /ASSIGNMENT2_DATA.csv"  # Removed extra spaces
image_features_path = "/content/drive/MyDrive/IR Assignment 2 /Images_Pickle"  # Removed extra spaces
tfidf_scores_path = "/content/drive/MyDrive/IR Assignment 2 /finalDictUpdated_Pickle.pkl"  # Removed extra spaces
output_path = "/content/drive/MyDrive/IR Assignment 2/Ques3.pkl"  # Removed extra spaces

# Load the dataset
data_df = pd.read_csv(dataset_path)  # Used the variable instead of hard-coded path

# Handle missing values in 'Review Text' column
data_df['Review Text'].fillna('', inplace=True)

# Load image features and TF-IDF scores
with open(image_features_path, 'rb') as f:
    loaded_image_features = pickle.load(f)
with open(tfidf_scores_path, 'rb') as f:
    loaded_tfidf_scores = pickle.load(f)

# Print only the first 5 key-value pairs from loaded_image_features
print("Loaded Image Features:")
for i, (key, value) in enumerate(loaded_image_features.items()):
    if i < 5:
        print(f"{key}: {value}")

# Print only the first 5 key-value pairs from loaded_tfidf_scores
print("\nLoaded TF-IDF Scores:")
for i, (key, value) in enumerate(loaded_tfidf_scores.items()):
    if i < 5:
        print(f"{key}: {value}")


Loaded Image Features:
https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg: [0.         0.01246884 0.         ... 0.         0.         0.        ]
https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg: [0.000000e+00 0.000000e+00 0.000000e+00 ... 0.000000e+00 8.240409e-05
 0.000000e+00]
https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg: [0. 0. 0. ... 0. 0. 0.]
https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg: [0.         0.         0.         ... 0.         0.00507829 0.        ]
https://images-na.ssl-images-amazon.com/images/I/71Md5ihUFLL._SY88.jpg: [0. 0. 0. ... 0. 0. 0.]

Loaded TF-IDF Scores:
Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.: [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976

In [ ]:
mdf = pd.read_csv("/content/drive/MyDrive/IR Assignment 2 /Modified_Dataset.csv")

In [ ]:
def get_review_text(image_url):
    # Find the row in the dataset corresponding to the given image URL
    row = mdf[mdf['Image'] == image_url]

    # Extract the review text from the row
    if not row.empty:
        review_text = row.iloc[0]['Review Text']
        return review_text
    else:
        return "Review text not found for this image URL"

# Example usage:
input_image_url = "https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg"  # Replace with the actual image URL
review_text = get_review_text(input_image_url)
print("Review Text:", review_text)


Review Text: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.


In [ ]:
import math
from collections import Counter

def calculate_tfidf(corpus, new_sentence):
    # Dummy function for text preprocessing (replace with your actual preprocessing function)

    # Tokenize the documents in the corpus
    tokenized_docs = [preprocess_text(doc) for doc in corpus]

    # Calculate Term Frequency (TF) for each token in each document
    tf_docs = []
    for doc in tokenized_docs:
        tf_doc = {}
        word_count = len(doc)
        word_freq = Counter(doc)
        for word, freq in word_freq.items():
            tf_doc[word] = freq / word_count
        tf_docs.append(tf_doc)

    # Calculate Inverse Document Frequency (IDF) for each token
    def inverseDocumentFrequency(term, allDocuments):
        numDocumentsWithThisTerm = sum(1 for doc in allDocuments if term in doc)
        if numDocumentsWithThisTerm > 0:
            return 1.0 + math.log(len(allDocuments) / numDocumentsWithThisTerm)
        else:
            return 1.0

    idf_dict = {}
    for doc in tokenized_docs:
        for word in set(doc):
            idf_dict[word] = inverseDocumentFrequency(word, tokenized_docs)

    # Preprocess the new sentence
    tokenized_new_sentence = preprocess_text(new_sentence)

    # Calculate TF for the new sentence
    tf_new_sentence = {}
    new_sentence_word_count = len(tokenized_new_sentence)
    new_sentence_word_freq = Counter(tokenized_new_sentence)
    for word, freq in new_sentence_word_freq.items():
        tf_new_sentence[word] = freq / new_sentence_word_count

    # Calculate TF-IDF for each word in the new sentence
    tfidf_new_sentence = {}
    for word, tf in tf_new_sentence.items():
        tfidf_new_sentence[word] = tf * idf_dict.get(word, 1.0)  # Use 1.0 as IDF if word not in corpus

    return tfidf_new_sentence


# New sentence to calculate TF-IDF for


In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

def calculate_cosine_similarity_Features(vector1, vector2):
    # Pad vector2 with zeros to match the dimensionality of vector1
    vector2_padded = np.pad(vector2, (0, len(vector1) - len(vector2)), mode='constant')

    # Reshape the vectors to be 2D arrays
    vector1 = vector1.reshape(1, -1)
    vector2_padded = vector2_padded.reshape(1, -1)

    # Calculate cosine similarity
    similarity = cosine_similarity(vector1, vector2_padded)
    return similarity[0][0]

# Example usage
vector1 = np.array([0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622])
vector2 = np.array([0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622])

# cosine_similarity_value = calculate_cosine_similarity(vector1, vector2)
# print(f"Cosine Similarity: {cosine_similarity_value}")


# Question 3:Image Retrieval and Text Retrieval

In [ ]:
Enter the image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
Enter the review text: Nice solid springs and defeinitely more silent. Easy installation and the bl

In [ ]:
# Take user input for image URL and review text
input_image_url = input("Enter the image URL: ")
input_review_text = input("Enter the review text: ")


Enter the image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
Enter the review text: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.


In [ ]:
inputImageFeature = image_features[input_image_url]

In [ ]:
print(inputImageFeature)

[0.         0.01246884 0.         ... 0.         0.         0.        ]


In [ ]:
print(image_features["https://images-na.ssl-images-amazon.com/images/I/61yOygGPK7L._SY88.jpg"])

[0.         0.00079294 0.         ... 0.         0.         0.00477319]


In [ ]:
print(inputImageFeature)

[0.         0.01246884 0.         ... 0.         0.         0.        ]


In [ ]:
tfidf_result = loaded_tfidf_scores[input_review_text]


In [ ]:
# numerical_list = [value for value in tfidf_result.values()]
# print(numerical_list)
numerical_list = tfidf_result

In [ ]:
print(f'Image Feature is =  {inputImageFeature}')
print(f'Review Feature is =  {numerical_list}')


Image Feature is =  [0.         0.01246884 0.         ... 0.         0.         0.        ]
Review Feature is =  [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622]


In [ ]:
text = input()

# Image Based Retrieval ->

In [ ]:
def retrieve_similar_images(input_image_features, image_features, top_k=3):
    similarities = {}
    for image_url, features in image_features.items():
        similarity = cosine_similarity([input_image_features], [features])[0][0]
        similarities[image_url] = similarity

    # Sort the dictionary by similarity score in descending order
    sorted_similarities = sorted(similarities.items(), key=lambda x: x[1], reverse=True)

    # Retrieve top k similar images
    similar_images = sorted_similarities[:top_k]

    # Add review text for each similar image
    similar_images_with_review = []
    for image_url, similarity in similar_images:
        review_text = get_review_text(image_url)
        similar_images_with_review.append((image_url, similarity, review_text))

    return similar_images_with_review

In [ ]:
# print(image_features)


{'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg': array([0.        , 0.01246884, 0.        , ..., 0.        , 0.        ,
       0.        ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71HSx4Y-5dL._SY88.jpg': array([0.000000e+00, 0.000000e+00, 0.000000e+00, ..., 0.000000e+00,
       8.240409e-05, 0.000000e+00], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71dVsYejzTL._SY88.jpg': array([0., 0., 0., ..., 0., 0., 0.], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71domStNfIL._SY88.jpg': array([0.        , 0.        , 0.        , ..., 0.        , 0.00507829,
       0.        ], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71Md5ihUFLL._SY88.jpg': array([0., 0., 0., ..., 0., 0., 0.], dtype=float32), 'https://images-na.ssl-images-amazon.com/images/I/71Isri9SEaL._SY88.jpg': array([0.        , 0.00078895, 0.        , ..., 0.        , 0.        ,
       0.        ], dtype=float32), 'http

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

In [ ]:
def retrieve_similar_images(input_image_features, image_features, top_k=3):
    similarities = {}
    for image_url, features in image_features.items():
        similarity = cosine_similarity([input_image_features], [features])[0][0]
        similarities[image_url] = similarity

    # Sort the dictionary by similarity score in descending order
    sorted_similarities = sorted(similarities.items(), key=lambda x: x[1], reverse=True)

    # Retrieve top k similar images
    similar_images = sorted_similarities[:top_k]

    # Add review text for each similar image
    similar_images_with_review = []
    for image_url, similarity in similar_images:
        review_text = get_review_text(image_url)
        similar_images_with_review.append((image_url, similarity, review_text))

    return similar_images_with_review

In [ ]:
similar_images = retrieve_similar_images(inputImageFeature, image_features)

In [ ]:
print(similar_images)

[('https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg', 0.99999976, 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.'), ('https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg', 0.34509608, "Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no problem with hum from this pickup - if you do, your problem is probably somewhere in your amp."), ('https://images-na.ssl-images-amazon.com/images/I/71IJnFDpNLL._SY88.jpg', 

In [ ]:
dataSetM = pd.read_csv("/content/drive/MyDrive/IR Assignment 2 /Modified_Dataset.csv")

In [ ]:

# Load the dataset
dataSetM = pd.read_csv("/content/drive/MyDrive/IR Assignment 2 /Modified_Dataset.csv")

# Create a dictionary to store the mapping from review text to URLs
review_text_to_urls = {}

# Iterate through the dataset and populate the dictionary
for index, row in dataSetM.iterrows():
    review_text = row['Review Text']
    url = row['Image']
    if review_text not in review_text_to_urls:
        review_text_to_urls[review_text] = [url]
    else:
        review_text_to_urls[review_text].append(url)

# Store the mapping dictionary in a pickle file
output_path = "/content/drive/MyDrive/IR Assignment 2 /review_text_to_urls.pkl"
with open(output_path, 'wb') as f:
    pickle.dump(review_text_to_urls, f)

print("Review text to URLs mapping has been saved to a pickle file.")


Review text to URLs mapping has been saved to a pickle file.


In [ ]:
# Retrieve similar images
combined_Result = []
Image_composted = []
print("\nImage-Based Retrieval:")
similar_images = retrieve_similar_images(inputImageFeature, image_features)

for image_url, similarity, review_text in similar_images:
    cosine_similarity_value = calculate_cosine_similarity_Features(np.array(loaded_tfidf_scores[review_text]), np.array(numerical_list))

    print(f"Image URL: {image_url}")
    print(f"Similarity: {similarity}")
    print(f"Review Text: {review_text}")
    print(f"Similarity with Given Review : {cosine_similarity_value}\n")
    result_dict = {
        'image_url': image_url,

        'similarity': similarity,
        'review_text': review_text,
        'cosine_similarity': cosine_similarity_value,
        'composite_similarity': (similarity + cosine_similarity_value )/2  # Add composite similarity to the dictionary
    }
    combined_Result.append(result_dict)
    Image_composted.append(result_dict)
    # combined_Result[("image_url":similarity,"review_text":cosine_similarity_value)] = ()




Image-Based Retrieval:
Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
Similarity: 0.9999997615814209
Review Text: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
Similarity with Given Review : 1.0

Image URL: https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg
Similarity: 0.34509608149528503
Review Text: Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no problem with hum from this pickup - if y

In [ ]:
combined_Result

[{'image_url': 'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg',
  'similarity': 0.99999976,
  'review_text': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.',
  'cosine_similarity': 1.0,
  'composite_similarity': 0.9999998807907104},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg',
  'similarity': 0.34509608,
  'review_text': "Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no proble

# Review Based Retrieval =>

In [ ]:
import pickle

def get_urls_for_review(review_text, mapping_file_path):
    # Load the mapping dictionary from the pickle file
    with open(mapping_file_path, 'rb') as f:
        review_text_to_urls = pickle.load(f)

    # Check if the review text exists in the mapping dictionary
    if review_text in review_text_to_urls:
        urls = review_text_to_urls[review_text]
        return urls
    else:
        return []

def get_keys_with_multiple_urls(mapping_file_path):
    # Load the mapping dictionary from the pickle file
    with open(mapping_file_path, 'rb') as f:
        review_text_to_urls = pickle.load(f)

    # Find keys with multiple URLs
    keys_with_multiple_urls = [key for key, urls in review_text_to_urls.items() if len(urls) > 1]
    return keys_with_multiple_urls

# Example usage
mapping_file_path = "/content/drive/MyDrive/IR Assignment 2 /review_text_to_urls.pkl"

# Print keys with multiple URLs
keys_with_multiple_urls = get_keys_with_multiple_urls(mapping_file_path)
print("Keys with multiple URLs:")
for key in keys_with_multiple_urls:
    print(f'{key}->next')


In [ ]:

def get_urls_for_review(review_text, mapping_file_path="/content/drive/MyDrive/IR Assignment 2 /review_text_to_urls.pkl"):
    # Load the mapping dictionary from the pickle file
    with open(mapping_file_path, 'rb') as f:
        review_text_to_urls = pickle.load(f)

    # Check if the review text exists in the mapping dictionary
    if review_text in review_text_to_urls:
        return review_text_to_urls[review_text]
    else:
        return []

# Example usage
# review_text = "Works great as a guitar bench mat. Not rugged enough for abuse but if you take care of it, it will take care of you. Makes organization of workspace much easier because screws won't roll around. Color is good too."
# mapping_file_path = "/content/drive/MyDrive/IR Assignment 2 /review_text_to_urls.pkl"
# urls = get_urls_for_review(review_text, mapping_file_path)
# print("URLs for the review text:")
# print(urls)
# for url in urls:


In [ ]:
print(numerical_list)

[0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283, 0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126, 0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622]


In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pickle

# Function to calculate cosine similarity
def calculate_cosine_similarity_Features(vector1, vector2):
    max_length = max(len(vector1), len(vector2))
    vector1_padded = np.pad(vector1, (0, max_length - len(vector1)), mode='constant')
    vector2_padded = np.pad(vector2, (0, max_length - len(vector2)), mode='constant')

    # Reshape the vectors to be 2D arrays
    vector1_padded = vector1_padded.reshape(1, -1)
    vector2_padded = vector2_padded.reshape(1, -1)

    # Calculate cosine similarity
    similarity = cosine_similarity(vector1_padded, vector2_padded)
    return similarity[0][0]

# Load TF-IDF scores
with open('/content/drive/MyDrive/IR Assignment 2 /finalDictUpdated_Pickle.pkl', 'rb') as f:
    loaded_tfidf_scores = pickle.load(f)

# Sample numerical list
# numerical_list = [0.17063740955725884, 0.5574870578984413, 0.6624272366585359, 0.2290869802813264, 0.171399912420283,
#                   0.14332661723291976, 0.32379520762790565, 0.11885746017713138, 0.32379520762790565, 0.3782857216841126,
#                   0.24341081968699865, 0.17523139377087624, 0.20096087987965253, 0.1719761624227622]
#numerical_list = [0.2527131629817488, 0.34750713839156405, 0.49682042749390193, 0.6589796065818447, 0.6012173415351826, 0.171399912420283, 0.2672729094324767, 0.2980851615579838, 0.3455462636073812, 0.2114264375712062, 0.3728140062080826]

# Define a function to retrieve similar images based on review text similarity
def retrieve_similar_images_by_review_text(loaded_tfidf_scores, numerical_list, top_k=3):
    # Initialize a list to store similarities between review text and numerical list
    similarities = []

    # Calculate similarity for each review text
    for review_text, tfidf_vector in loaded_tfidf_scores.items():
        similarity = calculate_cosine_similarity_Features(np.array(tfidf_vector), np.array(numerical_list))
        similarities.append((review_text, similarity))

    # Sort the list by similarity score in descending order
    similarities.sort(key=lambda x: x[1], reverse=True)

    # Retrieve top k similar images and their review text
    top_similar_images = similarities[:top_k]

    return top_similar_images

# Retrieve similar images based on review text similarity
top_similar_images = retrieve_similar_images_by_review_text(loaded_tfidf_scores, numerical_list)

# # Print the top similar images and their review text
# print("\nTop Similar Images Based on Review Text Similarity:")
# for review_text, similarity in top_similar_images:
#     Urlslist = get_urls_for_review(review_text)

#     print(f"Review Text: {review_text}")
#     print(f"Similarity with Numerical List: {similarity}\n")


In [ ]:
# print("\nTop Similar Images Based on Review Text Similarity:")
Text_Result  = []
# for review_text, similarity in top_similar_images:
#     urls_list = get_urls_for_review(review_text)
#     print(f"Review Text: {review_text}\n")
#     print("Similar Images:")
#     for url in urls_list:
#         print(f"Image URL: {url}")
#         image_feature = image_features[url]
#         image_feature = image_feature.reshape(1, -1)  # Reshape to 2D array
#         similarity_with_input = cosine_similarity(image_feature, inputImageFeature.reshape(1, -1))[0][0]
#         print(f"Similarity with Input Image Feature: {similarity_with_input}\n")
#     print(f"Review Text: {review_text}")
#     print(f"Similarity with Numerical List: {similarity}\n")
print("\nTop Similar Images Based on Review Text Similarity:")
for review_text, similarity in top_similar_images:
    urls_list = get_urls_for_review(review_text)
    print(f"Review: {review_text}\n")
    print(f"Cosine similarity of text: {similarity}\n")
    print("Similar Images:")
    for url in urls_list:
        image_feature = image_features[url]
        image_feature = image_feature.reshape(1, -1)  # Reshape to 2D array
        similarity_with_input = cosine_similarity(image_feature, inputImageFeature.reshape(1, -1))[0][0]
        print(f"1) Image URL: {url}")
        print(f"   Cosine similarity of images: {similarity_with_input}")
        result_dict = {
        'image_url': image_url,

        'similarity': similarity,
        'review_text': review_text,
        'cosine_similarity': cosine_similarity_value,
        'composite_similarity': (similarity + cosine_similarity_value )/2  # Add composite similarity to the dictionary
    }
    combined_Result.append(result_dict)
    Text_Result.append(result_dict)

        # for url1 ,text1 in combined_Result.items():
        #   if (url == url1):
        #     combined_Result[url] = max(text1 , (similarity + similarity_with_input )/2)
        # combined_Result[url] = (similarity + similarity_with_input )/2
    print("\n")



Top Similar Images Based on Review Text Similarity:
Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.

Cosine similarity of text: 1.0

Similar Images:
1) Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
   Cosine similarity of images: 0.9999997615814209


Review: This is a nice mic boom. I have tried a lightweight usb mic on this and I even put a MMX 990 mic on this and that mic is heavy. This boom even holds that mic up so I am impressed.

Cosine similarity of text: 0.934296309051642

Similar Images:
1) Image URL: https://images-na.ssl-images-amazon.com/images/I/51lELCmVyNL._SY88.jpg
   Cosine similarity of images: 0.1669592261314392


Review: I use this with the Zoom G3n and it works well as an expression pedal. Good value, solid build quality, so far so good.

Cosine similarity of text: 0.927191313

## Composite Similiarity

In [ ]:
combined_Result

[{'image_url': 'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg',
  'similarity': 0.99999976,
  'review_text': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.',
  'cosine_similarity': 1.0,
  'composite_similarity': 0.9999998807907104},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg',
  'similarity': 0.34509608,
  'review_text': "Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no proble

In [ ]:
# import json
# import numpy as np

# # Initialize an empty dictionary to store the data
# data_dict = {}

# # Iterate through the top similar images based on review text similarity
# for review_text, similarity in top_similar_images:
#     # Retrieve URLs related to the review text (assuming get_urls_for_review is defined)
#     urls_list = get_urls_for_review(review_text)

#     # Initialize a list to store information about each similar image
#     similar_images_info = []

#     # Iterate through each URL and calculate similarity with input image feature
#     for url in urls_list:
#         image_feature = image_features[url]
#         image_feature = image_feature.reshape(1, -1)  # Reshape to 2D array
#         similarity_with_input = cosine_similarity(image_feature, inputImageFeature.reshape(1, -1))[0][0]

#         # Append information about the similar image to the list
#         similar_images_info.append({
#             'image_url': url,
#             'cosine_similarity_with_input': float(similarity_with_input)  # Convert float32 to float
#         })

#     # Store data in the dictionary
#     data_dict[review_text] = {
#         'cosine_similarity_of_text': float(similarity),  # Convert float32 to float
#         'similar_images': similar_images_info
#     }

# # Print the dictionary in a more readable format using JSON
# print(json.dumps(data_dict, indent=4))


{
    "Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.": {
        "cosine_similarity_of_text": 1.0,
        "similar_images": [
            {
                "image_url": "https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg",
                "cosine_similarity_with_input": 0.9999997615814209
            }
        ]
    },
    "This is a nice mic boom. I have tried a lightweight usb mic on this and I even put a MMX 990 mic on this and that mic is heavy. This boom even holds that mic up so I am impressed.": {
        "cosine_similarity_of_text": 0.934296309051642,
        "similar_images": [
            {
                "image_url": "https://images-na.ssl-images-amazon.com/images/I/51lELCmVyNL._SY88.jpg",
                "cosine_similarity_with_input": 0.1669592261314392
            }
        ]
    },
    "I use this with

In [ ]:
combined_Result

[{'image_url': 'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg',
  'similarity': 0.99999976,
  'review_text': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.',
  'cosine_similarity': 1.0,
  'composite_similarity': 0.9999998807907104},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg',
  'similarity': 0.34509608,
  'review_text': "Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no proble

In [ ]:
# Sort the combined_Result list based on the 'similarity' key in descending order
sorted_combined_Result = sorted(combined_Result, key=lambda x: x['composite_similarity'], reverse=True)

# Initialize a dictionary to store the highest similarity for each URL
processed_urls = {}

# Iterate through the sorted list and keep only the highest similarity for each URL
for result in sorted_combined_Result:
    image_url = result['image_url']
    if image_url not in processed_urls:
        processed_urls[image_url] = result
    else:
        # If the URL is already processed, compare the similarity and keep the higher one
        if result['composite_similarity'] > processed_urls[image_url]['composite_similarity']:
            processed_urls[image_url] = result

# Sort the processed URLs based on the 'similarity' key in descending order
sorted_processed_urls = sorted(processed_urls.values(), key=lambda x: x['composite_similarity'], reverse=True)

# Print the sorted processed URLs
print("Top Similar Images Based on Composite Similiarity Text Similarity:")
for result in sorted_processed_urls:
    print(f"1) Image URL: {result['image_url']}")
    print(f"   Review: {result['review_text']}")
    print(f"   Cosine similarity of images: {result['similarity']:.4f}")
    print(f"   Cosine similarity of text: {result['cosine_similarity']:.3f}")
    print(f"   Composite similarity: {result['composite_similarity']:.4f}\n")


Top Similar Images Based on Review Text Similarity:
1) Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
   Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
   Cosine similarity of images: 1.0000
   Cosine similarity of text: 1.000
   Composite similarity: 1.0000

1) Image URL: https://images-na.ssl-images-amazon.com/images/I/71IJnFDpNLL._SY88.jpg
   Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
   Cosine similarity of images: 1.0000
   Cosine similarity of text: 0.675
   Composite similarity: 0.8377

1) Image URL: https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg
   Review: Hot damn!  I replaced the original neck position hum

# Result and Analysis:


In [ ]:
print("Top Ranked Result :")
for result in sorted_processed_urls:
    print(f"1) Image URL: {result['image_url']}")
    print(f"   Review: {result['review_text']}")
    print(f"   Cosine similarity of images: {result['similarity']:.4f}")
    print(f"   Cosine similarity of text: {result['cosine_similarity']:.3f}")
    print(f"   Composite similarity: {result['composite_similarity']:.4f}\n")


Top Ranked Result :
1) Image URL: https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg
   Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
   Cosine similarity of images: 1.0000
   Cosine similarity of text: 1.000
   Composite similarity: 1.0000

1) Image URL: https://images-na.ssl-images-amazon.com/images/I/71IJnFDpNLL._SY88.jpg
   Review: Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.
   Cosine similarity of images: 1.0000
   Cosine similarity of text: 0.675
   Composite similarity: 0.8377

1) Image URL: https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg
   Review: Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (whic

In [ ]:
Image_composted


[{'image_url': 'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg',
  'similarity': 0.99999976,
  'review_text': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.',
  'cosine_similarity': 1.0,
  'composite_similarity': 0.9999998807907104},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg',
  'similarity': 0.34509608,
  'review_text': "Hot damn!  I replaced the original neck position humbucker on my 1980 Les Paul (which I bought new) with a SPH90 Phat Cat.  What a difference!!  It is MUCH louder, and brighter, and all around sweeter and more tuneful that the original.  I used to rarely use the neck pickup alone.  Now I'll use it almost exclusively (though mixing in a bit of the bridge humbucker is sweet too).  I'm very glad I bought this and made the switch.  P.S. - I've had no proble

In [ ]:
Text_Result

[{'image_url': 'https://images-na.ssl-images-amazon.com/images/I/81q5+IxFVUL._SY88.jpg',
  'similarity': 1.0,
  'review_text': 'Loving these vintage springs on my vintage strat. They have a good tension and great stability. If you are floating your bridge and want the most out of your springs than these are the way to go.',
  'cosine_similarity': 1.0,
  'composite_similarity': 0.9999998807907104},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/712LuK8v2+L._SY88.jpg',
  'similarity': 0.934296309051642,
  'review_text': 'This is a nice mic boom. I have tried a lightweight usb mic on this and I even put a MMX 990 mic on this and that mic is heavy. This boom even holds that mic up so I am impressed.',
  'cosine_similarity': 0.6754402633300342,
  'composite_similarity': 0.8048682861908381},
 {'image_url': 'https://images-na.ssl-images-amazon.com/images/I/71IJnFDpNLL._SY88.jpg',
  'similarity': 0.9271913130989162,
  'review_text': 'I use this with the Zoom G3n and it works 

In [ ]:
# Sample data for illustration purposes

# Calculate the average composite similarity score for image-based retrieval
image_avg_composite_similarity = sum(item['composite_similarity'] for item in Image_composted) / len(Image_composted)

# Calculate the average composite similarity score for text-based retrieval
text_avg_composite_similarity = sum(item['composite_similarity'] for item in Text_Result) / len(Text_Result)

# Compare the average composite similarity scores
if image_avg_composite_similarity < text_avg_composite_similarity:
    print("Image-based retrieval is a better TEchnique.")
elif image_avg_composite_similarity > text_avg_composite_similarity:
    print("Text-based retrieval is a Better Technique.")
else:
    print("Both retrieval techniques provide similar similarity scores.")


Image-based retrieval is a better TEchnique.


The Image-based retrieval provides a better similarity score on average.
Reason: Image-based retrieval might be more effective because images can capture visual features that are not present in the text.

# Challenges & Potential Improvement:

## Challenges:

1. Understanding what users want is hard because sometimes they don't explain well or use unclear words.
2. Words can mean different things, like "python" can refer to both a programming language and a snake.
3. There's so much information online that it's easy to get overwhelmed with too many search results.
4. Finding images, videos, and audio can be tough because there's so much of it, and it's not just text.

### Potential Improvements:

1. Use natural language processing to better understand what users are asking for.
2. Keep updating search results in real-time so users get the latest information.
3. Use context like location or past searches to give more relevant results.
4. Ask users for feedback to improve search results and ranking.